In [1]:
import pandas as pd
import numpy as np 
import glob
import os 
from openpyxl import load_workbook
from openpyxl.styles import PatternFill, Font
from datetime import datetime

In [2]:
hoje = datetime.today().strftime('%Y-%m-%d')

In [3]:
#precisa ver duplicidade de desc e vendas irece.

In [203]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C14\TABELA DE PEDIDOS\Pedidos Semanais Especiais - BOT - 202514 (3).xlsx")

df_tabela = df_tabela[df_tabela['Ação revendedor'].notna() | df_tabela['Ação consumidor'].notna()]

df_tabela = df_tabela[df_tabela['Região'] == 'NNE'] 

df_tabela = df_tabela[(df_tabela['Canal'] != 'Ecomm')]

#df_tabela['Canal'] = np.where((df_tabela['Canal'] == "Loja") | (df_tabela['Canal'] == "Todos") | (df_tabela['Canal'] == "Loja | VD"),"TODOS","VD")

df_tabela = df_tabela[(df_tabela['Categoria'] != "EMBALAGENS") | (df_tabela['Categoria'] != "SUPORTE À VENDA")]

#df_tabela = df_tabela[df_tabela['Tipo de pedido'] == 'Semanal']

df_tabela = df_tabela[~df_tabela['Descrição'].str.contains('PRM')]

df_tabela = df_tabela[df_tabela['Tipo de produto']!= 'EDICAO LIMITADA']

df_tabela['Ação revendedor'] = np.where(df_tabela['Ação revendedor'].isna(),df_tabela['Ação consumidor'],df_tabela['Ação revendedor'])

df_tabela['Percentual de desconto revendedor'] = np.where(df_tabela['Percentual de desconto revendedor'].isna(),df_tabela['Percentual de desconto consumidor'],df_tabela['Percentual de desconto revendedor'])

df_tabela['MATCH'] = 1



In [205]:
import pyodbc
import configparser

#query de vendas por ciclo

config = configparser.ConfigParser()
config.read(r"C:\Users\joao.herculano\Documents\Enviador de email\credenciais.ini")

conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}"
)

query = f'''
SELECT 
    B.PDV, 
    B.SKU,
    bd.SKU2, 
    COALESCE(bd.SKU2, b.SKU) AS SKU_FINAL,
    B.DESCRICAO,
    SUM(CAST(b.VENDAS AS DECIMAL(18,2))) AS VENDAS_CICLO,
    C.Ciclo
FROM base_vendas_bi b
INNER JOIN ciclos_data_2025 c 
    ON CAST(b.[DATA] AS DATE) = CONVERT(DATE, c.[Date], 103) AND C.MARCA = 'BOT'
LEFT JOIN base_depara bd on b.SKU = bd.SKU 
WHERE CAST(b.[DATA] AS DATE) >= DATEADD(YEAR, -1, GETDATE())
GROUP BY
    B.PDV, 
    B.SKU,
    bd.SKU2,
    B.DESCRICAO,
    C.Ciclo
HAVING SUM(CAST(b.VENDAS AS DECIMAL(18,2))) > 0
'''
dfi = pd.read_sql(query, conn)
conn.close()

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_22664\2225685327.py:39: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  dfi = pd.read_sql(query, conn)


In [206]:
dfi['SKU2'] = dfi['SKU2'].fillna("-")

In [207]:
dfi = dfi[dfi['SKU2'] == "-"]

dfi.head()

PDV    SKU SKU2  SKU_FINAL                              DESCRICAO  \
0  20992  51021    -      51021               "QDB BLUSH LIQ GUARANA 6   
1  20057   4510    -       4510    REF BOTIK CR FAC FIRM AC/HIALUR 40g   
2  20997   1808    -       1808  MAKE B BAS LIQ MATE SALICYLIC 200 30g   
3  12823  56804    -      56804  MATCH MASC CAP SCIENCE RECONS V2 250g   
4  20998  83836    -      83836    OUI CREM DES HID CPO MADELEINE 200g   

   VENDAS_CICLO    Ciclo  
0           8.0  C202416  
1           2.0  C202417  
2           1.0  C202504  
3           2.0  C202511  
4           8.0  C202501

In [208]:

# 1. Agrupamento
df_agrupado = dfi.groupby(['PDV', 'SKU_FINAL', 'DESCRICAO', 'Ciclo'], as_index=False)['VENDAS_CICLO'].sum()

# 2. Pivotar o DataFrame
df_pivotado = df_agrupado.pivot_table(
    index=['PDV', 'SKU_FINAL', 'DESCRICAO'],
    columns='Ciclo',
    values='VENDAS_CICLO',
    fill_value=0  # Substitui NaN por 0
)

# 3. Resetar o índice para deixar como DataFrame normal (opcional)
df_pivotadowawa = df_pivotado.reset_index()

# 4. (Opcional) Renomear colunas com prefixo "Ciclo_"
df_pivotadowawa.columns.name = None
df_pivotadowawa = df_pivotadowawa.rename(columns=lambda x: f'Ciclo_{x}' if isinstance(x, (int, str)) and str(x).isdigit() else x)

# Resultado final
df_pivotadowawa


PDV  SKU_FINAL                                DESCRICAO  C202412  \
0       12522       1004            FLORATTA DES COL MY BLUE 75ml      0.0   
1       12522       1080     INTENSE GLOS LAB BUBBAL TUT/FRUT 5ml      2.0   
2       12522       1296      PMPCK THE BLEND DES ANTIT AER 2x75g      0.0   
3       12522       1302           PMPCK LILY DES ANTIT AER 2x75g      1.0   
4       12522       1314           PMPCK ZAAD DES ANTIT AER 2x75g      0.0   
...       ...        ...                                      ...      ...   
142986   5699      89048    ENVELOPE M BOTI NAMORADOS/25 UNITARIO      0.0   
142987   5699      89756        CAIXA FLAG BOTI NAMORADOS 25 UNIT      0.0   
142988   5699      89840           CAIXA LACO M BOTI PAIS/25 UNIT      0.0   
142989   5699      89843           ENVELOPE M BOTI PAIS 2025 UNIT      0.0   
142990   5699      90774  PIN MELHOR PAI O BOTICARIO PAIS/25 UNIT      0.0   

        C202413  C202414  C202415  C202416  C202417  C202501  ...  C202503  \
0          15.0      2.0      3.0     56.0      6.0      1.0  ...      1.0   
1           0.0      4.0      0.0     10.0      2.0      2.0  ...      2.0   
2           1.0      3.0      3.0      2.0      0.0      0.0  ...      0.0   
3           4.0      3.0      5.0      6.0      0.0      0.0  ...      0.0   
4           2.0      3.0      1.0      1.0      0.0      0.0  ...      0.0   
...         ...      ...      ...      ...      ...      ...  ...      ...   
142986      0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   
142987      0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   
142988      0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   
142989      0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   
142990      0.0      0.0      0.0      0.0      0.0      0.0  ...      0.0   

        C202504  C202505  C202506  C202507  C202508  C202509  C202510  \
0           5.0     12.0      7.0      2.0      0.0      1.0      2.0   
1           3.0      1.0      7.0     17.0      0.0      0.0      0.0   
2           0.0      0.0      0.0      0.0      0.0      0.0      0.0   
3           0.0      0.0      3.0      4.0      0.0      4.0      4.0   
4           0.0      0.0      0.0      0.0      0.0      0.0      0.0   
...         ...      ...      ...      ...      ...      ...      ...   
142986      0.0      0.0      0.0      0.0     26.0      4.0      0.0   
142987      0.0      0.0      0.0      0.0      1.0      0.0      0.0   
142988      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
142989      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
142990      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

        C202511  C202512  
0           5.0      2.0  
1           0.0      0.0  
2           0.0      0.0  
3           2.0      1.0  
4           1.0      0.0  
...         ...      ...  
142986      0.0      0.0  
142987      0.0      0.0  
142988     11.0      1.0  
142989     10.0      8.0  
142990      3.0      0.0  

[142991 rows x 21 columns]

In [209]:


df_pdv = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")

df_pdv_origi = pd.read_excel(r"C:\Users\joao.herculano\Documents\PDV_ATT.xlsx")

df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})

df_pdv = df_pdv[df_pdv['GESTÃO']!="Inativa"]

df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO', 'STATUS'])

df_pdv = df_pdv[df_pdv['CANAL']!='MTZ']

#df_pdv['CANAL'] = np.where((df_pdv['CANAL']=='LJ')|(df_pdv['CANAL']=='HIB')|(df_pdv['CANAL']=='CD'),'TODOS','VD')

df_pdv['MATCH'] = 1

df_pdv = df_pdv[(df_pdv['PDV']!=910291)&(df_pdv['PDV']!=910173)]



In [210]:
df_pdv = df_pdv.drop(columns=['PDV DESC'])

In [211]:
conn = pyodbc.connect(
    f"DRIVER={{SQL Server}};"
    f"SERVER={config['banco']['host']},1433;"
    f"DATABASE=GINSENG;"
    f"UID={config['banco']['user']};"
    f"PWD={config['banco']['password']}"
)

query_est_draft = f'''
select em.PDV ,
COALESCE(em.SKU_PARA , em.SKU) as SKU,
em.DESCRICAO,
d.salescurve as curva,
d.codcategory as categoria,
d.nextcycleprojection as proj_mar
,d.secondtonextcycleprojection as 'proj_mar+1',
em.[ESTOQUE ATUAL],em.[ESTOQUE EM TRANSITO],
em.[PEDIDO PENDENTE],
em.[DDV PREVISTO] ,
d.pricesellin as 'preço'
from estoque_mar em 
left join draft d on d.code = COALESCE(em.SKU_PARA , em.SKU) and d.loja_id = em.PDV 
where em.ORIGEM = 'BOT'
'''
df_draft_ = pd.read_sql(query_est_draft, conn)
conn.close()

#FALTA ATUALIZAR QUERY

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_22664\268247862.py:25: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df_draft_ = pd.read_sql(query_est_draft, conn)


In [212]:
df_draft = df_draft_

In [213]:
df_draft[(df_draft['PDV']=='23711') & (df_draft['SKU']=='48060')].head()

PDV    SKU                           DESCRICAO curva  \
39251  23711  48060  LILY CREM DES HID ACET CPO 250g V8     A   

                 categoria  proj_mar  proj_mar+1 ESTOQUE ATUAL  \
39251  CUIDADOS COM A PELE      87.0         0.0           511   

      ESTOQUE EM TRANSITO PEDIDO PENDENTE DDV PREVISTO  preço  
39251                   4               0         9,20  42.54

In [214]:
df_draft = df_draft[~df_draft['DESCRICAO'].str.contains('OUI', na=False)]

df_draft.shape

(350518, 12)

In [215]:
df_draft['ESTOQUE ATUAL'] = df_draft['ESTOQUE ATUAL'].astype(float)

df_draft['ESTOQUE EM TRANSITO'] = df_draft['ESTOQUE EM TRANSITO'].astype(float)

df_draft['PEDIDO PENDENTE'] = df_draft['PEDIDO PENDENTE'].astype(float)

df_draft.dtypes

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_22664\1765304903.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['ESTOQUE ATUAL'] = df_draft['ESTOQUE ATUAL'].astype(float)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_22664\1765304903.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['ESTOQUE EM TRANSITO'] = df_draft['ESTOQUE EM TRANSITO'].astype(float)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_22664\1765304903.py:5: SettingWithCopyWarning: 
A value is trying t

PDV                     object
SKU                     object
DESCRICAO               object
curva                   object
categoria               object
proj_mar               float64
proj_mar+1             float64
ESTOQUE ATUAL          float64
ESTOQUE EM TRANSITO    float64
PEDIDO PENDENTE        float64
DDV PREVISTO            object
preço                  float64
dtype: object

In [216]:
df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].str.replace(',','.')

df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].astype(float)

df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].fillna(0)

C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_22664\1952797845.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].str.replace(',','.')
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_22664\1952797845.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_draft['DDV PREVISTO'] = df_draft['DDV PREVISTO'].astype(float)
C:\Users\joao.herculano\AppData\Local\Temp\ipykernel_22664\1952797845.py:5: SettingWithCopyWarning: 
A value is trying to be set 

In [217]:
df_draft = df_draft.groupby(['PDV','SKU','curva','categoria'])[['proj_mar','proj_mar+1','ESTOQUE ATUAL','ESTOQUE EM TRANSITO','PEDIDO PENDENTE','DDV PREVISTO','preço']].max().reset_index()

In [218]:
df_tabela = df_tabela.drop_duplicates()

In [219]:
df_bi_preco = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C13\preço BI\TABELA DE PREÇOS (2).xlsx")

df_bi_preco = df_bi_preco.drop(columns=['Descrição','Tipo Preço','CATEGORIA','LINHA','MARCA'])



In [220]:
df_pivotadowawa['SKU_FINAL'] = df_pivotadowawa['SKU_FINAL'].astype('str')

In [221]:
df_draft = pd.merge(df_draft,df_pivotadowawa,left_on=['PDV','SKU'],right_on=['PDV','SKU_FINAL'])

In [222]:
df_draft[df_draft['SKU']=='48060'].head()

PDV    SKU curva            categoria  proj_mar  proj_mar+1  \
76    12522  48060     A  CUIDADOS COM A PELE      14.0        19.0   
1196  12817  48060     A  CUIDADOS COM A PELE      61.0        76.0   
2375  12818  48060     A  CUIDADOS COM A PELE       9.0        12.0   
3362  12820  48060     A  CUIDADOS COM A PELE      11.0        13.0   
4320  12823  48060     A  CUIDADOS COM A PELE      10.0        12.0   

      ESTOQUE ATUAL  ESTOQUE EM TRANSITO  PEDIDO PENDENTE  DDV PREVISTO  ...  \
76             42.0                  0.0              0.0          0.68  ...   
1196           87.0                 60.0              0.0          2.82  ...   
2375            3.0                  0.0              0.0          0.44  ...   
3362           40.0                  0.0              0.0          0.49  ...   
4320           20.0                  0.0              0.0          0.46  ...   

      C202503 C202504 C202505  C202506  C202507  C202508  C202509  C202510  \
76       14.0    30.0    11.0     38.0     10.0     19.0     23.0      3.0   
1196     30.0    82.0    36.0    219.0     33.0     79.0    106.0     44.0   
2375      5.0     8.0     4.0     20.0      2.0      8.0      9.0      7.0   
3362      9.0    15.0     8.0     22.0      4.0     24.0     16.0      7.0   
4320      5.0    26.0     6.0     15.0      1.0      5.0     13.0      7.0   

      C202511  C202512  
76       19.0     10.0  
1196     64.0      9.0  
2375      9.0      0.0  
3362      2.0      2.0  
4320      9.0      0.0  

[5 rows x 31 columns]

In [223]:
df_tabela[df_tabela['Código']=='48060']

Empty DataFrame
Columns: [Ciclo, Região, Canal, Código, Descrição, IAF, Tipo de pedido, Foco, Unidade de negócio, Marca, Categoria, Subcategoria, Quantidade por caixa, Tipo de promoção, Catálogo, Tipo de produto, Ação consumidor, Percentual de desconto consumidor, Ação revendedor, Percentual de desconto revendedor, Sortimento P, Sortimento M, Sortimento G, MATCH]
Index: []

[0 rows x 24 columns]

In [224]:
df_final = pd.merge(left=df_tabela,right=df_pdv,on='MATCH',how='left')

df_final = df_final.drop_duplicates()

df_final.shape

(47509, 31)

In [225]:
df_final[df_final['Código']=='48060'].head()

Empty DataFrame
Columns: [Ciclo, Região, Canal, Código, Descrição, IAF, Tipo de pedido, Foco, Unidade de negócio, Marca, Categoria, Subcategoria, Quantidade por caixa, Tipo de promoção, Catálogo, Tipo de produto, Ação consumidor, Percentual de desconto consumidor, Ação revendedor, Percentual de desconto revendedor, Sortimento P, Sortimento M, Sortimento G, MATCH, PDV, CANAL, DESCRIÇÃO PDV, UF, MARCA, ANALISTA, SUPERVISOR]
Index: []

[0 rows x 31 columns]

In [226]:
df_final['PDV'].value_counts()

PDV
12522    617
12817    617
12818    617
12820    617
12823    617
        ... 
24257    617
24268    617
24269    617
24293    617
23813    617
Name: count, Length: 77, dtype: int64

In [227]:
df_final['PDV'] = df_final['PDV'].astype('str')
df_final['Código'] = df_final['Código'].astype('str')


df_final = pd.merge(left=df_final,right=df_draft,left_on=['PDV','Código'],right_on=['PDV','SKU'],how='left')
df_final.shape

(49398, 61)

In [228]:
df_final[df_final['Código']=='48060'].head()

Ciclo Região Canal Código                           Descrição  IAF  \
17861  C202514    NNE    VD  48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17862  C202514    NNE    VD  48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17863  C202514    NNE    VD  48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17864  C202514    NNE    VD  48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17865  C202514    NNE    VD  48060  LILY CREM DES HID ACET CPO 250g V8  NaN   

       Tipo de pedido  Foco  Unidade de negócio Marca  ... C202503  C202504  \
17861             NaN   NaN                 NaN  BOTI  ...    14.0     30.0   
17862             NaN   NaN                 NaN  BOTI  ...    30.0     82.0   
17863             NaN   NaN                 NaN  BOTI  ...     5.0      8.0   
17864             NaN   NaN                 NaN  BOTI  ...     9.0     15.0   
17865             NaN   NaN                 NaN  BOTI  ...     5.0     26.0   

       C202505  C202506  C202507  C202508 C202509  C202510 C202511  C202512  
17861     11.0     38.0     10.0     19.0    23.0      3.0    19.0     10.0  
17862     36.0    219.0     33.0     79.0   106.0     44.0    64.0      9.0  
17863      4.0     20.0      2.0      8.0     9.0      7.0     9.0      0.0  
17864      8.0     22.0      4.0     24.0    16.0      7.0     2.0      2.0  
17865      6.0     15.0      1.0      5.0    13.0      7.0     9.0      0.0  

[5 rows x 61 columns]

In [229]:
df_final['PDV'].value_counts()

PDV
23711    659
21278    656
20993    656
20997    656
21375    654
        ... 
24257    617
24268    617
24269    617
24293    617
23813    617
Name: count, Length: 77, dtype: int64

In [230]:
df_final = df_final.drop(columns=['Sortimento P', 'Sortimento M',
       'Sortimento G','MARCA','SKU'])

In [231]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")


In [232]:
calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)
calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]


calendario = calendario[calendario['MARCA'] == "BOTICARIO"]

calendario = calendario.drop(columns='MARCA')

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 2).astype(str).str.zfill(2) # >>>>>>>>> MUDAR PRA CICLO CORRETO 

ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]


# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]


filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)

filtered_calendario


Ciclo INICIO CICLO  FIM CICLO  DURAÇÃO       Date  NUM_CICLO  \
2367  C202514   2025-09-22 2025-10-12       21 2025-09-22         14   

     ANO_CICLO CICLOMAIS2  dias_ate_inicio  
2367     C2025    C202516               31

In [233]:
filtered_calendario['MATCH'] = 1

In [234]:
df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

In [235]:
df_draft['PDV'] = df_draft['PDV'].astype(str)

In [236]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','MATCH','dias_ate_inicio']], on='MATCH',how='left')
df_final.shape

(49398, 61)

In [237]:
df_final[df_final['SKU_FINAL']=='48060'].head()

Ciclo_x Região Canal Código                           Descrição  IAF  \
17861  C202514    NNE    VD  48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17862  C202514    NNE    VD  48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17863  C202514    NNE    VD  48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17864  C202514    NNE    VD  48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17865  C202514    NNE    VD  48060  LILY CREM DES HID ACET CPO 250g V8  NaN   

       Tipo de pedido  Foco  Unidade de negócio Marca  ... C202508  C202509  \
17861             NaN   NaN                 NaN  BOTI  ...    19.0     23.0   
17862             NaN   NaN                 NaN  BOTI  ...    79.0    106.0   
17863             NaN   NaN                 NaN  BOTI  ...     8.0      9.0   
17864             NaN   NaN                 NaN  BOTI  ...    24.0     16.0   
17865             NaN   NaN                 NaN  BOTI  ...     5.0     13.0   

       C202510  C202511  C202512  Ciclo_y INICIO CICLO  FIM CICLO DURAÇÃO  \
17861      3.0     19.0     10.0  C202514   2025-09-22 2025-10-12      21   
17862     44.0     64.0      9.0  C202514   2025-09-22 2025-10-12      21   
17863      7.0      9.0      0.0  C202514   2025-09-22 2025-10-12      21   
17864      7.0      2.0      2.0  C202514   2025-09-22 2025-10-12      21   
17865      7.0      9.0      0.0  C202514   2025-09-22 2025-10-12      21   

       dias_ate_inicio  
17861               31  
17862               31  
17863               31  
17864               31  
17865               31  

[5 rows x 61 columns]

In [238]:
df_final['Código'] = df_final['Código'].astype('Int64') 
df_final['PDV'] = df_final['PDV'].astype('Int64') 

In [239]:
df_bi_preco['SKU2'] = df_bi_preco['SKU2'].astype('Int64')
df_bi_preco.head()

SKU1   SKU2  UF      PC      PV chave sku2 chave sku1
0  84918  84918  AL  393.70  1300.0    AL84918    AL84918
1  84918  84918  BA  436.73  1300.0    BA84918    BA84918
2  84918  84918  SE  379.94  1300.0    SE84918    SE84918
3  54230  54230  AL  138.54   499.9    AL54230    AL54230
4  54230  54230  BA  148.66   499.9    BA54230    BA54230

In [240]:


df_final = pd.merge(left=df_final,right=df_bi_preco,right_on=['UF','SKU2'],left_on=['UF','Código'],how='left')
df_final.shape   

(49398, 67)

In [241]:
df_final[df_final['SKU_FINAL']=='48060'].head()

Ciclo_x Região Canal  Código                           Descrição  IAF  \
17861  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17862  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17863  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17864  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17865  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   

       Tipo de pedido  Foco  Unidade de negócio Marca  ... INICIO CICLO  \
17861             NaN   NaN                 NaN  BOTI  ...   2025-09-22   
17862             NaN   NaN                 NaN  BOTI  ...   2025-09-22   
17863             NaN   NaN                 NaN  BOTI  ...   2025-09-22   
17864             NaN   NaN                 NaN  BOTI  ...   2025-09-22   
17865             NaN   NaN                 NaN  BOTI  ...   2025-09-22   

       FIM CICLO  DURAÇÃO  dias_ate_inicio   SKU1   SKU2     PC     PV  \
17861 2025-10-12       21               31  11085  48060  38.03  139.9   
17862 2025-10-12       21               31  11085  48060  38.03  139.9   
17863 2025-10-12       21               31  11085  48060  38.03  139.9   
17864 2025-10-12       21               31  11085  48060  38.03  139.9   
17865 2025-10-12       21               31  11085  48060  38.03  139.9   

      chave sku2  chave sku1  
17861    AL48060     AL11085  
17862    AL48060     AL11085  
17863    AL48060     AL11085  
17864    AL48060     AL11085  
17865    AL48060     AL11085  

[5 rows x 67 columns]

In [242]:
df_bi_preco['SKU1'] = df_bi_preco['SKU1'].fillna(0)

In [243]:
# Conversão segura para Int64 (nullable)
df_bi_preco['SKU1'] = pd.to_numeric(df_bi_preco['SKU1'], errors='coerce').astype('Int64')

# Realiza o merge
df_final = pd.merge(
    left=df_final,
    right=df_bi_preco[['SKU1', 'SKU2', 'UF', 'PC', 'PV']],
    right_on=['UF', 'SKU1'],
    left_on=['UF', 'Código'],
    how='left'
)

# Verifica o resultado
print(df_final.shape)


(49398, 71)


In [244]:
df_final[df_final['SKU_FINAL']=='48060'].head()

Ciclo_x Região Canal  Código                           Descrição  IAF  \
17861  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17862  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17863  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17864  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17865  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   

       Tipo de pedido  Foco  Unidade de negócio Marca  ... SKU1_x  SKU2_x  \
17861             NaN   NaN                 NaN  BOTI  ...  11085   48060   
17862             NaN   NaN                 NaN  BOTI  ...  11085   48060   
17863             NaN   NaN                 NaN  BOTI  ...  11085   48060   
17864             NaN   NaN                 NaN  BOTI  ...  11085   48060   
17865             NaN   NaN                 NaN  BOTI  ...  11085   48060   

        PC_x   PV_x  chave sku2  chave sku1 SKU1_y  SKU2_y PC_y  PV_y  
17861  38.03  139.9     AL48060     AL11085   <NA>    <NA>  NaN   NaN  
17862  38.03  139.9     AL48060     AL11085   <NA>    <NA>  NaN   NaN  
17863  38.03  139.9     AL48060     AL11085   <NA>    <NA>  NaN   NaN  
17864  38.03  139.9     AL48060     AL11085   <NA>    <NA>  NaN   NaN  
17865  38.03  139.9     AL48060     AL11085   <NA>    <NA>  NaN   NaN  

[5 rows x 71 columns]

In [245]:
df_final['PRECO DE COMPRA'] = np.where(~df_final['PC_x'].isna(),df_final['PC_x'],df_final['PC_y'])

df_final['PRECO DE VENDA'] = np.where(~df_final['PV_x'].isna(),df_final['PV_x'],df_final['PV_y'])



In [246]:
df_final['CANAL'] = np.where((df_final['CANAL'] == 'LJ') | (df_final['CANAL'] == 'HIB'), "TODOS" , np.where((df_final['CANAL'] == 'CD') | (df_final['CANAL'] == 'VD'), "VD", df_final['CANAL']))

df_final['CANAL'].value_counts()

CANAL
TODOS    39069
VD       10329
Name: count, dtype: int64

In [247]:
df_final = df_final.drop_duplicates()

In [248]:
df_final[df_final['SKU_FINAL']=='48060'].head()

Ciclo_x Região Canal  Código                           Descrição  IAF  \
17861  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17862  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17863  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17864  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17865  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   

       Tipo de pedido  Foco  Unidade de negócio Marca  ...   PC_x   PV_x  \
17861             NaN   NaN                 NaN  BOTI  ...  38.03  139.9   
17862             NaN   NaN                 NaN  BOTI  ...  38.03  139.9   
17863             NaN   NaN                 NaN  BOTI  ...  38.03  139.9   
17864             NaN   NaN                 NaN  BOTI  ...  38.03  139.9   
17865             NaN   NaN                 NaN  BOTI  ...  38.03  139.9   

       chave sku2  chave sku1  SKU1_y  SKU2_y PC_y  PV_y PRECO DE COMPRA  \
17861     AL48060     AL11085    <NA>    <NA>  NaN   NaN           38.03   
17862     AL48060     AL11085    <NA>    <NA>  NaN   NaN           38.03   
17863     AL48060     AL11085    <NA>    <NA>  NaN   NaN           38.03   
17864     AL48060     AL11085    <NA>    <NA>  NaN   NaN           38.03   
17865     AL48060     AL11085    <NA>    <NA>  NaN   NaN           38.03   

       PRECO DE VENDA  
17861           139.9  
17862           139.9  
17863           139.9  
17864           139.9  
17865           139.9  

[5 rows x 73 columns]

In [249]:
df_final = df_final.drop(columns=['SKU1_x','SKU1_y','SKU2_x','SKU2_y','PC_x', 'PV_x','PC_y', 'PV_y','Subcategoria',
'Quantidade por caixa'
])

In [250]:
df_final['UFPRODUTO'] = df_final['UF'].astype(str) + df_final['Código'].astype(str)


In [251]:
df_final = df_final.rename(columns={'Compra inteligente Próximo Ciclo + 1':'Compra inteligente Próximo Ciclo','Arquivo_Origem': 'MARCA'})

In [252]:
df_final = df_final[~df_final['Marca'].isna()]
df_final['Marca'].isna().sum()

np.int64(0)

In [253]:
df_final[df_final['SKU_FINAL']=='48060'].head()

Ciclo_x Região Canal  Código                           Descrição  IAF  \
17861  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17862  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17863  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17864  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17865  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   

       Tipo de pedido  Foco  Unidade de negócio Marca  ...  Ciclo_y  \
17861             NaN   NaN                 NaN  BOTI  ...  C202514   
17862             NaN   NaN                 NaN  BOTI  ...  C202514   
17863             NaN   NaN                 NaN  BOTI  ...  C202514   
17864             NaN   NaN                 NaN  BOTI  ...  C202514   
17865             NaN   NaN                 NaN  BOTI  ...  C202514   

       INICIO CICLO  FIM CICLO  DURAÇÃO dias_ate_inicio  chave sku2  \
17861    2025-09-22 2025-10-12       21              31     AL48060   
17862    2025-09-22 2025-10-12       21              31     AL48060   
17863    2025-09-22 2025-10-12       21              31     AL48060   
17864    2025-09-22 2025-10-12       21              31     AL48060   
17865    2025-09-22 2025-10-12       21              31     AL48060   

      chave sku1  PRECO DE COMPRA  PRECO DE VENDA  UFPRODUTO  
17861    AL11085            38.03           139.9    AL48060  
17862    AL11085            38.03           139.9    AL48060  
17863    AL11085            38.03           139.9    AL48060  
17864    AL11085            38.03           139.9    AL48060  
17865    AL11085            38.03           139.9    AL48060  

[5 rows x 64 columns]

In [254]:
df_final[df_final['SKU_FINAL']=='48060'].head()

Ciclo_x Região Canal  Código                           Descrição  IAF  \
17861  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17862  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17863  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17864  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   
17865  C202514    NNE    VD   48060  LILY CREM DES HID ACET CPO 250g V8  NaN   

       Tipo de pedido  Foco  Unidade de negócio Marca  ...  Ciclo_y  \
17861             NaN   NaN                 NaN  BOTI  ...  C202514   
17862             NaN   NaN                 NaN  BOTI  ...  C202514   
17863             NaN   NaN                 NaN  BOTI  ...  C202514   
17864             NaN   NaN                 NaN  BOTI  ...  C202514   
17865             NaN   NaN                 NaN  BOTI  ...  C202514   

       INICIO CICLO  FIM CICLO  DURAÇÃO dias_ate_inicio  chave sku2  \
17861    2025-09-22 2025-10-12       21              31     AL48060   
17862    2025-09-22 2025-10-12       21              31     AL48060   
17863    2025-09-22 2025-10-12       21              31     AL48060   
17864    2025-09-22 2025-10-12       21              31     AL48060   
17865    2025-09-22 2025-10-12       21              31     AL48060   

      chave sku1  PRECO DE COMPRA  PRECO DE VENDA  UFPRODUTO  
17861    AL11085            38.03           139.9    AL48060  
17862    AL11085            38.03           139.9    AL48060  
17863    AL11085            38.03           139.9    AL48060  
17864    AL11085            38.03           139.9    AL48060  
17865    AL11085            38.03           139.9    AL48060  

[5 rows x 64 columns]

In [255]:
df_vdc = pd.read_csv(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\DB_PROMOÇÕES\BOTICARIO\C10\VENDA VITORIA 2024\VENDA VITORIA.csv")

df_vdc['PRODUTO'] = df_vdc['PRODUTO'].astype('Int64')

df_final['Código'] = df_final['Código'].astype('Int64')

df_final =pd.merge(left=df_final,right=df_vdc,left_on= ['PDV','Código'],right_on= ['PDV GINSENG','PRODUTO'],how='left' )

df_final[df_final.columns[-1]] = df_final[df_final.columns[-1]].fillna(0)

In [256]:
df_vdc[df_vdc['PRODUTO']== 74043].head()

PDV GINSENG  PRODUTO  202401  202402  202403  202404  202405  202406  \
1235        23701    74043      12      24      12      16       8      14   
3033        23702    74043       2      22       8      22      10      14   
5171        23703    74043      10      18       6      18       6       2   

      202407  202408  202409  202410  202411  202412  202413  202414  202415  \
1235       6      14      12       0       8      10       4      42       0   
3033      14      10      12       8      22       6      14      36      10   
5171      20       0      10       2      22       4       2      26       2   

      202416  
1235      14  
3033       0  
5171      16

In [257]:
df_final = df_final.fillna(0)


In [258]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'curva', 'categoria',
       'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço', 'SKU_FINAL', 'DESCRICAO',
       'C202412', 'C202413', 'C202414', 'C202415', 'C202416', 'C202417',
       'C202501', 'C202502', 'C202503', 'C202504', 'C202505', 'C202506',
       'C202507', 'C202508', 'C202509', 'C202510', 'C202511', 'C202512',
       'Ciclo_y', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio',
       'chave sku2', 'chave sku1', 'PRECO DE COMPRA', 'PRECO DE VENDA',
       'UFPRODUTO', 'PDV GINSENG', 'PRODUTO', '2024

In [259]:
import re

# identificar colunas de ciclo puro (ex: '202407')
colunas_ciclo_puro = [col for col in df_final.columns[-16:-1]]

for col in colunas_ciclo_puro:
    col_hist = f'C{col}'
    if col_hist in df_final.columns:
        # mantém o maior valor entre a coluna histórica e a pura
        df_final[col_hist] = df_final[[col_hist, col]].max(axis=1)

# remove as colunas puras
if colunas_ciclo_puro:
    df_final.drop(columns=colunas_ciclo_puro, inplace=True)


In [260]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'curva', 'categoria',
       'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço', 'SKU_FINAL', 'DESCRICAO',
       'C202412', 'C202413', 'C202414', 'C202415', 'C202416', 'C202417',
       'C202501', 'C202502', 'C202503', 'C202504', 'C202505', 'C202506',
       'C202507', 'C202508', 'C202509', 'C202510', 'C202511', 'C202512',
       'Ciclo_y', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio',
       'chave sku2', 'chave sku1', 'PRECO DE COMPRA', 'PRECO DE VENDA',
       'UFPRODUTO', 'PDV GINSENG', 'PRODUTO', '2024

In [261]:
df_irece = pd.read_csv(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\DADOS DOURADO\VENDA\COMPILADO_VENDAS.csv", sep=';')

df_irece['DATA_VENDA'] = pd.to_datetime(df_irece['DATA_VENDA'], dayfirst=True)

df_irece = pd.merge(df_irece,calendario[['Ciclo','Date']],how='left', left_on='DATA_VENDA',right_on='Date')

df_irece.head()

DATA_VENDA    PDV  pdvs cp                                       DESC PDV  \
0 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   
1 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   
2 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   
3 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   
4 2025-04-01  12993    24253   PERFUMARIA E COSMETICOS QUEIROZ DOURADO LTDA   

   Código                                 Descrição  Quantidade Faturamento  \
0    1004             FLORATTA DES COL MY BLUE 75ml           1       98,99   
1    4539      BOTIK CR FAC FIRMADOR AC/HIAL 40g V2           1      129,05   
2   29046  BOTICOLL CONNEX DES BDY SPR 100ml V6 PCK           1        38,9   
3   47154                 CBEM DES ROLL S/ALUM 55ml           1       21,98   
4   47411                          ARBO NECESS LONA           1       57,26   

     Ciclo       Date  
0  C202505 2025-04-01  
1  C202505 2025-04-01  
2  C202505 2025-04-01  
3  C202505 2025-04-01  
4  C202505 2025-04-01

In [262]:
df_irece_agrupado = df_irece.groupby(['PDV','Código','Ciclo'])['Quantidade'].sum().reset_index()

df_pivotado = df_irece_agrupado.pivot(index=['PDV', 'Código'], columns='Ciclo', values='Quantidade').reset_index()

df_pivotado = df_pivotado.fillna(0)

In [263]:
df_final.columns[37:55]

Index(['C202413', 'C202414', 'C202415', 'C202416', 'C202417', 'C202501',
       'C202502', 'C202503', 'C202504', 'C202505', 'C202506', 'C202507',
       'C202508', 'C202509', 'C202510', 'C202511', 'C202512', 'Ciclo_y'],
      dtype='object')

In [264]:
for col_c in df_final.columns[37:55]:
    sufixo = col_c[1:]  # Remove o 'C' do início, ex: 'C202407' -> '202407'
    df_final.columns = df_final.columns.str.replace("C20", "20", regex=True)


df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'curva', 'categoria',
       'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço', 'SKU_FINAL', 'DESCRICAO',
       '202412', '202413', '202414', '202415', '202416', '202417', '202501',
       '202502', '202503', '202504', '202505', '202506', '202507', '202508',
       '202509', '202510', '202511', '202512', 'Ciclo_y', 'INICIO CICLO',
       'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'chave sku2', 'chave sku1',
       'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG',
       'PRODUTO', '202416'],
      dtype=

In [265]:
df_final = pd.merge(df_final,df_pivotado,how='left',on=['PDV','Código'])

df_final = df_final.fillna(0)

df_final.head()

Ciclo_x Região Canal  Código                 Descrição  IAF  \
0  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   
1  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   
2  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   
3  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   
4  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   

   Tipo de pedido  Foco  Unidade de negócio Marca  ... C202415  C202416  \
0             0.0   0.0                 0.0  BOTI  ...     0.0      0.0   
1             0.0   0.0                 0.0  BOTI  ...     0.0      0.0   
2             0.0   0.0                 0.0  BOTI  ...     0.0      0.0   
3             0.0   0.0                 0.0  BOTI  ...     0.0      0.0   
4             0.0   0.0                 0.0  BOTI  ...     0.0      0.0   

   C202417  C202501 C202502  C202503 C202504  C202505  C202506  C202507  
0      0.0      0.0     0.0      0.0     0.0      0.0      0.0      0.0  
1      0.0      0.0     0.0      0.0     0.0      0.0      0.0      0.0  
2      0.0      0.0     0.0      0.0     0.0      0.0      0.0      0.0  
3      0.0      0.0     0.0      0.0     0.0      0.0      0.0      0.0  
4      0.0      0.0     0.0      0.0     0.0      0.0      0.0      0.0  

[5 rows x 91 columns]

In [266]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'curva', 'categoria',
       'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço', 'SKU_FINAL', 'DESCRICAO',
       '202412', '202413', '202414', '202415', '202416', '202417', '202501',
       '202502', '202503', '202504', '202505', '202506', '202507', '202508',
       '202509', '202510', '202511', '202512', 'Ciclo_y', 'INICIO CICLO',
       'FIM CICLO', 'DURAÇÃO', 'dias_ate_inicio', 'chave sku2', 'chave sku1',
       'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG',
       'PRODUTO', '202416', 'C202401', 'C

In [267]:


# 1. Identificar colunas no formato 'C2024xx', 'C2025xx', etc.
colunas_ciclo_c = [col for col in df_pivotado.columns if re.fullmatch(r'C20\d{4}', col)]

for col_c in colunas_ciclo_c:
    sufixo = col_c[1:]  # Remove o 'C' do início, ex: 'C202407' -> '202407'
    col_hist = col_c
    
    if col_hist in df_final.columns:
        # Pega o maior valor entre a coluna de histórico e a de ciclo com "C"
        df_final[col_hist] = df_final[[col_hist, col_c]].max(axis=1)

# (Opcional) Remover as colunas 'C20xxxx' após o merge
df_final.drop(columns=colunas_ciclo_c, inplace=True)


In [268]:
colunas_ciclo_c = [col for col in df_pivotado.columns if re.fullmatch(r'C20\d{4}', col)]

for col_c in colunas_ciclo_c:
    sufixo = col_c[1:]  # Remove o 'C' do início, ex: 'C202407' -> '202407'
    col_hist = col_c
    print(sufixo,col_c)
colunas_ciclo_c

202401 C202401
202402 C202402
202403 C202403
202404 C202404
202405 C202405
202406 C202406
202407 C202407
202408 C202408
202409 C202409
202410 C202410
202411 C202411
202412 C202412
202413 C202413
202414 C202414
202415 C202415
202416 C202416
202417 C202417
202501 C202501
202502 C202502
202503 C202503
202504 C202504
202505 C202505
202506 C202506
202507 C202507


['C202401',
 'C202402',
 'C202403',
 'C202404',
 'C202405',
 'C202406',
 'C202407',
 'C202408',
 'C202409',
 'C202410',
 'C202411',
 'C202412',
 'C202413',
 'C202414',
 'C202415',
 'C202416',
 'C202417',
 'C202501',
 'C202502',
 'C202503',
 'C202504',
 'C202505',
 'C202506',
 'C202507']

In [269]:
df_final = df_final.drop(columns=['Ciclo_y'])

In [270]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'curva', 'categoria',
       'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço', 'SKU_FINAL', 'DESCRICAO',
       '202412', '202413', '202414', '202415', '202416', '202417', '202501',
       '202502', '202503', '202504', '202505', '202506', '202507', '202508',
       '202509', '202510', '202511', '202512', 'INICIO CICLO', 'FIM CICLO',
       'DURAÇÃO', 'dias_ate_inicio', 'chave sku2', 'chave sku1',
       'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG',
       'PRODUTO', '202416'],
      dtype='object')

In [271]:
df_final = df_final.drop_duplicates()
df_final.shape

(49398, 66)

In [272]:
df_final['chave'] = df_final['PDV'].astype('str') + df_final['Código'].astype('str')

In [273]:
df_final = df_final.fillna(0)


In [274]:
df_final.columns[36:54]

Index(['202412', '202413', '202414', '202415', '202416', '202417', '202501',
       '202502', '202503', '202504', '202505', '202506', '202507', '202508',
       '202509', '202510', '202511', '202512'],
      dtype='object')

In [275]:
# Define list of target columns
sales_2024_cols = df_final.columns[36:54]
# Create a new column with the row-wise max
df_final['PICO DE VENDAS 2024'] = df_final[sales_2024_cols].max(axis=1)



In [276]:
vendas_6_meses = df_final.columns[48:54]

df_final['Pico Vendas Ultimos 6 ciclos'] = df_final[vendas_6_meses].max(axis=1)

In [277]:
df_final.columns[37:44]

Index(['202413', '202414', '202415', '202416', '202417', '202501', '202502'], dtype='object')

In [278]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'curva', 'categoria',
       'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço', 'SKU_FINAL', 'DESCRICAO',
       '202412', '202413', '202414', '202415', '202416', '202417', '202501',
       '202502', '202503', '202504', '202505', '202506', '202507', '202508',
       '202509', '202510', '202511', '202512', 'INICIO CICLO', 'FIM CICLO',
       'DURAÇÃO', 'dias_ate_inicio', 'chave sku2', 'chave sku1',
       'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG',
       'PRODUTO', '202416', 'chave', 'PICO DE VENDAS

In [279]:
df_final.columns

Index(['Ciclo_x', 'Região', 'Canal', 'Código', 'Descrição', 'IAF',
       'Tipo de pedido', 'Foco', 'Unidade de negócio', 'Marca', 'Categoria',
       'Tipo de promoção', 'Catálogo', 'Tipo de produto', 'Ação consumidor',
       'Percentual de desconto consumidor', 'Ação revendedor',
       'Percentual de desconto revendedor', 'MATCH', 'PDV', 'CANAL',
       'DESCRIÇÃO PDV', 'UF', 'ANALISTA', 'SUPERVISOR', 'curva', 'categoria',
       'proj_mar', 'proj_mar+1', 'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',
       'PEDIDO PENDENTE', 'DDV PREVISTO', 'preço', 'SKU_FINAL', 'DESCRICAO',
       '202412', '202413', '202414', '202415', '202416', '202417', '202501',
       '202502', '202503', '202504', '202505', '202506', '202507', '202508',
       '202509', '202510', '202511', '202512', 'INICIO CICLO', 'FIM CICLO',
       'DURAÇÃO', 'dias_ate_inicio', 'chave sku2', 'chave sku1',
       'PRECO DE COMPRA', 'PRECO DE VENDA', 'UFPRODUTO', 'PDV GINSENG',
       'PRODUTO', '202416', 'chave', 'PICO DE VENDAS

In [280]:
df_final.columns[36:54]

Index(['202412', '202413', '202414', '202415', '202416', '202417', '202501',
       '202502', '202503', '202504', '202505', '202506', '202507', '202508',
       '202509', '202510', '202511', '202512'],
      dtype='object')

In [281]:
df_final.head()

Ciclo_x Região Canal  Código                 Descrição  IAF  \
0  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   
1  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   
2  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   
3  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   
4  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   

   Tipo de pedido  Foco  Unidade de negócio Marca  ... chave sku1  \
0             0.0   0.0                 0.0  BOTI  ...    AL28813   
1             0.0   0.0                 0.0  BOTI  ...    AL28813   
2             0.0   0.0                 0.0  BOTI  ...    AL28813   
3             0.0   0.0                 0.0  BOTI  ...    AL28813   
4             0.0   0.0                 0.0  BOTI  ...    AL28813   

   PRECO DE COMPRA  PRECO DE VENDA  UFPRODUTO PDV GINSENG  PRODUTO 202416  \
0            58.17           224.9    AL48141         0.0        0    0.0   
1            58.17           224.9    AL48141         0.0        0    0.0   
2            58.17           224.9    AL48141         0.0        0    0.0   
3            58.17           224.9    AL48141         0.0        0    0.0   
4            58.17           224.9    AL48141         0.0        0    0.0   

        chave  PICO DE VENDAS 2024  Pico Vendas Ultimos 6 ciclos  
0  1252248141                 20.0                           7.0  
1  1281748141                 45.0                          18.0  
2  1281848141                 11.0                           3.0  
3  1282048141                  8.0                           3.0  
4  1282348141                 11.0                           2.0  

[5 rows x 69 columns]

In [282]:
'''# Define as colunas mensais
colunas_mensais = df_final.columns[36:54]

# Função de cálculo por grupo
def calcular_crescimento(grupo):
    soma_mensal = grupo[colunas_mensais].sum()
    variacao_mensal = soma_mensal.pct_change().dropna()
    variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

    if len(variacao_mensal) == 0:
        return pd.Series({'CRESCIMENTO': np.nan})

    media = variacao_mensal.mean()
    desvio = variacao_mensal.std()

    limite_sup = media + 2 * desvio
    limite_inf = media - 2 * desvio

    variacoes_filtradas = variacao_mensal[variacao_mensal.between(limite_inf, limite_sup)]
    crescimento = round(variacoes_filtradas.mean(), 4)
    return pd.Series({'CRESCIMENTO': crescimento})

# Aplica a função por PDV
crescimento_por_pdv = (
    df_final
    .groupby('PDV')
    .apply(calcular_crescimento)   # retorna índice com PDV
    .reset_index(level=0)          # reseta só o nível PDV
)

# Merge do resultado de volta no dataframe original
df_final = df_final.merge(crescimento_por_pdv, on='PDV', how='left')'''


"# Define as colunas mensais\ncolunas_mensais = df_final.columns[36:54]\n\n# Função de cálculo por grupo\ndef calcular_crescimento(grupo):\n    soma_mensal = grupo[colunas_mensais].sum()\n    variacao_mensal = soma_mensal.pct_change().dropna()\n    variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]\n\n    if len(variacao_mensal) == 0:\n        return pd.Series({'CRESCIMENTO': np.nan})\n\n    media = variacao_mensal.mean()\n    desvio = variacao_mensal.std()\n\n    limite_sup = media + 2 * desvio\n    limite_inf = media - 2 * desvio\n\n    variacoes_filtradas = variacao_mensal[variacao_mensal.between(limite_inf, limite_sup)]\n    crescimento = round(variacoes_filtradas.mean(), 4)\n    return pd.Series({'CRESCIMENTO': crescimento})\n\n# Aplica a função por PDV\ncrescimento_por_pdv = (\n    df_final\n    .groupby('PDV')\n    .apply(calcular_crescimento)   # retorna índice com PDV\n    .reset_index(level=0)          # reseta só o nível PDV\n)\n\n# Merge do resultado de volta n

In [283]:
# Suponha que os meses estão nas colunas 10 a 26 (17 colunas = 17 meses)
colunas_mensais = df_final.columns[36:54]

# Passo 1: Soma todas as linhas (itens) por mês → resultado: total por mês
soma_mensal = df_final[colunas_mensais].sum()

# Passo 2: Calcula a variação percentual de um mês para o outro
variacao_mensal = soma_mensal.pct_change()
variacao_mensal = variacao_mensal.dropna()

variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

# Passo 3: Calcula a média da variação (ignorando o primeiro NaN)
media_variacao = variacao_mensal[1:].mean()

# Calcula média e desvio padrão
media = variacao_mensal.mean()
desvio = variacao_mensal.std()

# Define limite (ex: 2 desvios padrão)
limite_superior = media + 2 * desvio
limite_inferior = media - 2 * desvio

# Filtra dados dentro do limite
filtro = variacao_mensal.between(limite_inferior, limite_superior)
df_filtrado = variacao_mensal[filtro]
CRESCIMENTO = round(df_filtrado.mean(),4)

df_final['CRESCIMENTO_GERAL'] = 0.2

CRESCIMENTO


np.float64(0.1171)

In [284]:
df_final.columns[36:54]

Index(['202412', '202413', '202414', '202415', '202416', '202417', '202501',
       '202502', '202503', '202504', '202505', '202506', '202507', '202508',
       '202509', '202510', '202511', '202512'],
      dtype='object')

In [285]:
vendas_todos_historicos = df_final.columns[36:54]

df_final['MEDIANA DO HISTÓRICO'] = df_final[vendas_todos_historicos].median(axis=1)

df_final['MEDIA DO HISTÓRICO'] = df_final[vendas_todos_historicos].mean(axis=1)

medi = df_final.groupby(['CANAL','UF','Código'])['MEDIANA DO HISTÓRICO'].max().reset_index()
medi = medi.rename(columns={'MEDIANA DO HISTÓRICO':'med_por_canal'})

df_final = pd.merge(left=df_final, right=medi,on=['CANAL','UF','Código'],how='left')

medi

CANAL   UF  Código  med_por_canal
0     TODOS   AL    1004            0.0
1     TODOS   AL    1788            0.0
2     TODOS   AL    2094            0.0
3     TODOS   AL    2100            0.0
4     TODOS   AL    2150            0.0
...     ...  ...     ...            ...
6165     VD  VDC   87925            0.0
6166     VD  VDC   87926            0.0
6167     VD  VDC   87927            0.0
6168     VD  VDC   87959            0.0
6169     VD  VDC   87960            0.0

[6170 rows x 4 columns]

In [286]:
df_final.columns[38]

'202414'

In [287]:
mesmo_ciclo_ano_passado = df_final.columns[38]
ciclo_ano_passado = df_final.columns[38]
df_final[ciclo_ano_passado] = df_final[mesmo_ciclo_ano_passado]

In [288]:
df_final['CRESCIMENTO_GERAL'] = 0.2
df_final['CRESCIMENTO'] = 0.2

In [289]:
df_final['CRESCIMENTO_FINAL'] = df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'] #crescimento do pdv

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']>0.8,0.8,df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'])

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']<0,0,df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'])

df_final['MEDIANA DO HISTÓRICO2'] = np.where(df_final['MEDIANA DO HISTÓRICO']==0,df_final['MEDIA DO HISTÓRICO'] ,df_final['MEDIANA DO HISTÓRICO'])

# Primeiro cálculo intermediário
df_final['PV GINSENG'] = np.where(df_final['CRESCIMENTO_FINAL'] * df_final[ciclo_ano_passado] + df_final[ciclo_ano_passado] <1,
                                    round(df_final['CRESCIMENTO_FINAL'] * df_final['MEDIANA DO HISTÓRICO2']+ df_final['MEDIANA DO HISTÓRICO2'],0), 
                                    round(df_final['CRESCIMENTO_FINAL']*df_final[ciclo_ano_passado]+df_final[ciclo_ano_passado],0))


df_final.shape

(49398, 77)

In [290]:
df_final.head()

Ciclo_x Região Canal  Código                 Descrição  IAF  \
0  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   
1  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   
2  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   
3  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   
4  C202514    NNE    VD   48141  ACCORDES DES COL 80ml V5  0.0   

   Tipo de pedido  Foco  Unidade de negócio Marca  ... PICO DE VENDAS 2024  \
0             0.0   0.0                 0.0  BOTI  ...                20.0   
1             0.0   0.0                 0.0  BOTI  ...                45.0   
2             0.0   0.0                 0.0  BOTI  ...                11.0   
3             0.0   0.0                 0.0  BOTI  ...                 8.0   
4             0.0   0.0                 0.0  BOTI  ...                11.0   

   Pico Vendas Ultimos 6 ciclos  CRESCIMENTO_GERAL  MEDIANA DO HISTÓRICO  \
0                           7.0                0.2                   3.0   
1                          18.0                0.2                   8.0   
2                           3.0                0.2                   2.0   
3                           3.0                0.2                   1.0   
4                           2.0                0.2                   1.0   

  MEDIA DO HISTÓRICO  med_por_canal CRESCIMENTO  CRESCIMENTO_FINAL  \
0           5.000000            8.0         0.2                0.4   
1          12.789474            8.0         0.2                0.4   
2           2.578947            8.0         0.2                0.4   
3           2.421053            8.0         0.2                0.4   
4           2.473684            8.0         0.2                0.4   

   MEDIANA DO HISTÓRICO2  PV GINSENG  
0                    3.0        13.0  
1                    8.0        59.0  
2                    2.0         7.0  
3                    1.0         8.0  
4                    1.0         8.0  

[5 rows x 77 columns]

In [291]:
df_final = df_final.drop(columns=['MEDIANA DO HISTÓRICO2'] )

In [292]:
df_final.columns[38:45]

Index(['202414', '202415', '202416', '202417', '202501', '202502', '202503'], dtype='object')

In [293]:
df_final.columns[49:54]

Index(['202508', '202509', '202510', '202511', '202512'], dtype='object')

In [294]:
df_final = df_final.rename(columns={df_final.columns[49]: "C-4", df_final.columns[50]: "C-3",df_final.columns[51]: "C-2",df_final.columns[52]: "C-1",df_final.columns[53]: "Atual"})

In [295]:
df_final.columns[37]

'202413'

In [296]:
df_final.drop(columns=df_final.columns[39:49], inplace=True)
df_final.drop(columns=df_final.columns[37], inplace=True)

In [297]:
df_final['COBERTURA ATUAL'] = df_final['ESTOQUE ATUAL'].astype(float) / df_final['DDV PREVISTO'].astype(float)

In [298]:
df_final['COBERTURA ATUAL'] = df_final['COBERTURA ATUAL'].replace([np.inf, -np.inf], 0)

In [299]:
df_final['COBERTURA ATUAL'].value_counts()

COBERTURA ATUAL
0.000000      10548
100.000000     1253
50.000000       806
33.333333       689
200.000000      605
              ...  
338.235294        1
622.727273        1
104.347826        1
377.777778        1
2.127660          1
Name: count, Length: 2608, dtype: int64

In [300]:
df_final["DDV PREVISTO"] = df_final["DDV PREVISTO"].astype(float)

df_final["DDV PREVISTO"] = df_final["DDV PREVISTO"].fillna(0)

In [301]:
colunas_chave = [c for c in df_final.columns if c not in ["DDV PREVISTO", "COBERTURA ATUAL"]]


# encontrar índice da linha com maior DDV e depois maior COBERTURA
idx = (
df_final
.sort_values(["DDV PREVISTO", "COBERTURA ATUAL"], ascending=[False, False])
.groupby(colunas_chave, as_index=False)
.head(1)
)


# reordenar colunas como no original
df_final_dedup = idx[df_final.columns.tolist()].reset_index(drop=True)

In [302]:
# Columns to bring up front
priority_cols = [
    'SKU',	'Marca',	'INICIO CICLO',
    'FIM CICLO',	'DURAÇÃO',	'PRECO DE COMPRA',	'PRECO DE VENDA',
    'UFPRODUTO',	'Item Desativado',	'Data Prevista Regularização',
    'ANALISTA',	'UF',	'CANAL',	'PDV',	'DESCRIÇÃO PDV',	'Classe',
    'Descrição',	'Categoria',
	'ESTOQUE ATUAL', 'ESTOQUE EM TRANSITO',	'COBERTURA ATUAL',
    'Pedido Pendente',	'PICO DE VENDAS 2024','Pico Vendas Ultimos 6 ciclos',
    'C-4',	'C-3',	'C-2',	'C-1',	'Histórico de Vendas do Ciclo Atual',
    'Dias sem venda'
]

# All remaining columns
other_cols = [col for col in df_final_dedup.columns if col not in priority_cols]

# Reorder
'Ação consumidor', 'Percentual de desconto consumidor', 'Ação revendedor', 'Percentual de desconto revendedor', '202408'


('Ação consumidor',
 'Percentual de desconto consumidor',
 'Ação revendedor',
 'Percentual de desconto revendedor',
 '202408')

In [303]:
df_final_dedup.drop(columns=['dias_ate_inicio','SKU_FINAL',
                             'CRESCIMENTO'],inplace=True)

In [304]:
df_final_dedup['INICIO CICLO'] = pd.to_datetime(df_final_dedup['INICIO CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

df_final_dedup['FIM CICLO'] = pd.to_datetime(df_final_dedup['FIM CICLO'], dayfirst=True).dt.strftime('%d/%m/%Y')

In [305]:
df_final_dedup['Percentual de desconto revendedor'] = np.where((df_final_dedup['Percentual de desconto revendedor'].isna()) & (~df_final_dedup['Percentual de desconto consumidor'].isna()),df_final_dedup['Percentual de desconto consumidor'],df_final_dedup['Percentual de desconto revendedor'])

In [306]:
df_pdv_origi['PDV'] = df_pdv_origi['PDV'].astype('Int64')
df_final_dedup['PDV'] = df_final_dedup['PDV'].astype('Int64')


df_final_dedup = pd.merge(left=df_final_dedup,right=df_pdv_origi[['PDV','CANAL','UF']],how='left',on='PDV')

In [307]:
df_final_dedup['Código'].isna().sum()

np.int64(0)

In [308]:
df_irece_agrupado = df_irece.groupby(['PDV','Código','Ciclo'])['Quantidade'].sum().reset_index()

In [309]:
df_final_dedup = df_final_dedup.rename(columns={'CANAL_x':'CANAL','UF_X':'UF','Marca':'LINHA'})


In [310]:
df_final_dedup = df_final_dedup.rename(columns={'UF_x':'UF','DESCRICAO_y':'DESCRICAO'})

In [311]:
df_final_dedup = df_final_dedup.drop(columns={'CANAL_y', 'UF_y'})


In [312]:
df_final_dedup['Estoque Total'] = df_final_dedup['ESTOQUE ATUAL'].astype(float) + df_final_dedup['ESTOQUE EM TRANSITO'].astype(float) + df_final_dedup['PEDIDO PENDENTE'].astype(float)

In [313]:
ciclo_ano_passado

'202414'

In [314]:
df_final_dedup = df_final_dedup[['DURAÇÃO','CANAL','ANALISTA','SUPERVISOR','UF','chave','PDV','DESCRIÇÃO PDV','Código','DESCRICAO','LINHA','Categoria','curva','Percentual de desconto consumidor','Ação consumidor',
                                 'Percentual de desconto revendedor','Ação revendedor','C-4', 'C-3', 'C-2', 'C-1','Atual','ESTOQUE ATUAL',ciclo_ano_passado ,'ESTOQUE EM TRANSITO','PEDIDO PENDENTE','Estoque Total',
                                 'DDV PREVISTO','COBERTURA ATUAL','proj_mar', 'proj_mar+1','MEDIA DO HISTÓRICO','PICO DE VENDAS 2024','Pico Vendas Ultimos 6 ciclos','PRECO DE COMPRA',
                                'PRECO DE VENDA','PV GINSENG']]

In [315]:
df_final_dedup['Percentual de desconto revendedor'] = np.where(df_final_dedup['Percentual de desconto revendedor'] == '0,00', df_final_dedup['Percentual de desconto consumidor'],df_final_dedup['Percentual de desconto revendedor'])

In [316]:
ciclo_ano_passado

'202414'

In [317]:
df_final_dedup = df_final_dedup.drop_duplicates()

In [318]:
df_final_dedup['Valor Sugestão'] = ""

df_final_dedup['Sugestão Comercial'] = ""

In [319]:
df_final_dedup[['DDV PREVISTO',
       'COBERTURA ATUAL',]].dtypes

DDV PREVISTO       float64
COBERTURA ATUAL    float64
dtype: object

In [320]:
df_final_dedup[ 'DDV PREVISTO'] =  df_final_dedup['DDV PREVISTO'].fillna(0)

df_final_dedup = df_final_dedup.drop_duplicates()

In [321]:
df_final_dedup[df_final_dedup['chave'] == '2371184387'].head()

DURAÇÃO CANAL   ANALISTA           SUPERVISOR   UF       chave    PDV  \
1       21    VD  JEFFERSON  Juliana Vasconcelos  VDC  2371184387  23711   

             DESCRIÇÃO PDV  Código                DESCRICAO  ... proj_mar  \
1  ER VITORIA DA CONQUISTA   84387  MALBEC DES COL V6 100ml  ...   1505.0   

  proj_mar+1 MEDIA DO HISTÓRICO  PICO DE VENDAS 2024  \
1        0.0         545.894737               2734.0   

  Pico Vendas Ultimos 6 ciclos  PRECO DE COMPRA PRECO DE VENDA  PV GINSENG  \
1                        857.0              0.0            0.0       412.0   

   Valor Sugestão  Sugestão Comercial  
1                                      

[1 rows x 39 columns]

In [322]:
df_final_dedup[df_final_dedup['chave'] == '2371184387']['DDV PREVISTO'].head()


1    94.98
Name: DDV PREVISTO, dtype: float64

In [323]:
# Export to Excel
output_file = f'C:\\Users\\joao.herculano\\Documents\\promoção_BOTI_{ciclo_mais2}.{hoje}.xlsx'
with pd.ExcelWriter(output_file, engine='openpyxl') as writer:
    df_final_dedup.to_excel(writer, index=False)

# Apply styles
wb = load_workbook(output_file)
ws = wb['Sheet1']

# Style header
header_fill = PatternFill(start_color='ADD8E6', end_color='ADD8E6', fill_type='solid')  # Light Blue
header_font = Font(color='FFFFFF', bold=True)  # White & Bold

for cell in ws[1]:
    cell.fill = header_fill
    cell.font = header_font

# Style rows: gray/white alternating
gray_fill = PatternFill(start_color='DDDDDD', end_color='DDDDDD', fill_type='solid')  # Light gray

for i, row in enumerate(ws.iter_rows(min_row=2, max_row=ws.max_row), start=2):
    if i % 2 == 0:
        for cell in row:
            cell.fill = gray_fill

# Save styled workbook
wb.save(output_file)


coisas q saem

Lançamento
Subcategoria
Projeção Próximo Ciclo 
Promoção Próximo Ciclo
Compra inteligente semanal/Sugestão de compra
Compra inteligente Próximo Ciclo
Planograma
Carteira Bloqueada Para Novos Pedidos
Quantidade por caixa
Preço Sell In
Quantidade
Item analisado
Tipo Preço

>>>>>>>>>>>>>NAO ESTÁ PEGANDO O MERGE COM O DF_ESTOQUE


CRIAR PROJEÇÃO DE VENDA DO CICLO ATUAL
Compra inteligente Próximo Ciclo + 1 >>>>>>> RENAME PRA NOROMAL